# hello world DL LLMs
this docs for DL develompent
RD (reveres docs)



https://github.com/ksaa-nlp/KSAA-CAD/blob/main/README.md
https://codalab.lisn.upsaclay.fr/competitions/18510



some code takes from 
here:
- https://github.com/ksaa-nlp/KSAA-CAD/blob/main/WSD-BERT/KSAA_CAD_WSD_TASK.ipynb
- https://www.kaggle.com/code/mo7amed3twan/arabic-text-categorization-with-98-accuracy/notebook

import libs

In [1]:
import os
import re
import json
import random
from collections import defaultdict
from itertools import count

import string
import math

import pandas as pd
import numpy as np



from sklearn.model_selection import train_test_split


import nltk
from nltk.corpus import stopwords
from nltk.tokenize import word_tokenize
import pyarabic.araby as arab

import torch
import torch.nn as nn
import torch.nn.functional as F
from torch.nn.utils.rnn import pad_sequence
from torch.utils.data import DataLoader, Dataset, Sampler

from transformers import BertTokenizer, BertModel, AutoModel, AutoConfig, AutoModelForSeq2SeqLM
from transformers.modeling_outputs import Seq2SeqLMOutput


import tensorflow as tf
from tensorflow.keras.models import Sequential, load_model
from tensorflow.keras.layers import Embedding, LSTM, Dense
from tensorflow.keras.preprocessing.text import Tokenizer
from tensorflow.keras.preprocessing.sequence import pad_sequences
from tensorflow.keras.utils import to_categorical



from utils import  JSONDataset,  TokenSampler,  get_dataloader, AraT5RevDict,  RevdictModel, PositionalEncoding, ARBERTRevDict



# from sklearn.preprocessing import LabelEncoder
# from sklearn.model_selection import train_test_split
# from sklearn.pipeline import Pipeline
# from sklearn.feature_extraction.text import TfidfVectorizer
# from sklearn.linear_model import LogisticRegression
# from sklearn.metrics import classification_report

/usr/lib/python3.12/site-packages/tqdm/auto.py:21: TqdmWarning: IProgress not found. Please update jupyter and ipywidgets. See https://ipywidgets.readthedocs.io/en/stable/user_install.html
  from .autonotebook import tqdm as notebook_tqdm
2024-05-04 20:53:36.466534: I tensorflow/core/util/port.cc:113] oneDNN custom operations are on. You may see slightly different numerical results due to floating-point round-off errors from different computation orders. To turn them off, set the environment variable `TF_ENABLE_ONEDNN_OPTS=0`.
2024-05-04 20:53:36.497307: I tensorflow/core/platform/cpu_feature_guard.cc:210] This TensorFlow binary is optimized to use available CPU instructions in performance-critical operations.
To enable the following instructions: AVX2 AVX_VNNI FMA, in other operations, rebuild TensorFlow with the appropriate compiler flags.
2024-05-04 20:53:37.208462: W tensorflow/compiler/tf2tensorrt/utils/py_utils.cc:38] TF-TRT Warning: Could not find TensorRT


# Checking for GPU

In [2]:
# If there's a GPU available...
if torch.cuda.is_available():

    # Tell PyTorch to use the GPU.
    device = torch.device("cuda")

    print('There are %d GPU(s) available.' % torch.cuda.device_count())

    print('We will use the GPU:', torch.cuda.get_device_name(0))

# If not...
else:
    print('No GPU available, using the CPU instead.')
    device = torch.device("cpu")
     

No GPU available, using the CPU instead.


In [3]:
dev = pd.read_json("dev.json")
# train = pd.read_json("train.json")
# test = pd.read_json("test_rd.json")

In [4]:
dev.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 3921 entries, 0 to 3920
Data columns (total 7 columns):
 #   Column   Non-Null Count  Dtype 
---  ------   --------------  ----- 
 0   id       3921 non-null   object
 1   word     3921 non-null   object
 2   pos      3636 non-null   object
 3   gloss    3921 non-null   object
 4   electra  3921 non-null   object
 5   bertseg  3921 non-null   object
 6   bertmsa  3921 non-null   object
dtypes: object(7)
memory usage: 214.6+ KB


In [5]:
# print(dev.loc[0,["word", "gloss", "bertmsa"]])
print(dev.loc[0,"bertmsa"])
# print(dev.loc[0,"bertseg"])

[-1.0540555716, 0.7359393239, -0.48558506370000004, 0.2842389047, -0.014874745200000001, -0.3338057995, -1.0626255274, 1.0642404556, -0.4464528263, 0.0199941862, 0.1688296795, -1.0119912624, 0.8879950047, -0.8462011218000001, -0.8778951764, -0.4855767488, -1.6353212595, 1.3357245922, 1.0484230518, -0.8187140226, -1.0998333693, -0.20108243820000002, 0.0084375525, -0.5216298103, -1.0158572197, -0.1254878342, 0.3969086707, 0.8399226665, -1.5730353594, -0.0320673026, 0.0535756908, 0.599609971, -0.9122300148, 0.5332223773, -0.1954540461, 0.1690832078, -0.8100447655, -0.21358451250000002, 0.106545575, -0.5762116313, 0.1857455522, -1.0667365789, -0.7359434366000001, -0.0319795124, 0.9318914413, -1.1079915762, 0.4777292609, 0.3399627209, -0.0690475032, 0.4316110313, 1.3506428003, -0.1698862612, 0.0734871924, -0.0796024501, 1.1741449833, -0.0029123838, 0.4108131528, 0.35932824020000004, -0.8871686459, 0.6745029092, -1.1904027462, -1.2675589323, -0.3061779439, 0.1978542656, 0.15237942340000002, 

# preprocess_text functions

In [6]:
stop_words = list(set(stopwords.words('arabic')))
a_dict = r"""
                             ّ    | # Tashdid
                             َ    | # Fatha
                             ً    | # Tanwin Fath
                             ُ    | # Damma
                             ٌ    | # Tanwin Damm
                             ِ    | # Kasra
                             ٍ    | # Tanwin Kasr
                             ْ    | # Sukun
                            ـ    | # Tatwil/Kashida
                     """
regex_pattern = (
    "\U0001F600-\U0001F64F"+  # emoticons {😀 , 😆} 
    "\U0001F300-\U0001F5FF"+  # symbols & pictographs {🌍 , 🌞}
    "\U0001F680-\U0001F6FF"+  # transport & map symbols {🚌 , 🚕 }
    "\U0001F1E0-\U0001F1FF"   # flags (iOS) { 🇺🇸 , 🇨🇦 }
) 
def preprocess_text(text):
    # Remove special characters {& $ @} and punctuation {. , ? !}
    text = re.sub(r'[^\w\s]', '', text)

    # Remove Arabic diacritics
    text = re.sub(a_dict, '', text)

    # Remove emoji characters 
    text = re.sub(f"[{regex_pattern}]", '', text)    
    
    # Tokeniz The Sentence into tokens
    tokens = word_tokenize(text)
    tokens = [word for word in tokens if word not in stop_words and len(word) > 1]
    preprocessed_text = ' '.join(tokens)
    
    return preprocessed_text

# Finetune

## camel bert MSA

In [7]:
# Load the BERT tokenizer.
model_name = "CAMeL-Lab/bert-base-arabic-camelbert-msa"
tokenizer = BertTokenizer.from_pretrained(model_name)
model = BertModel.from_pretrained(model_name)

In [4]:
# Get the vocabulary as a list
vocab_list = list(tokenizer.get_vocab().keys())

print(vocab_list)
print(len(vocab_list))

['[PAD]', '[UNK]', '[CLS]', '[SEP]', '[MASK]', '!', '"', '#', '$', '%', '&', "'", '(', ')', '*', '+', ',', '-', '.', '/', '0', '1', '2', '3', '4', '5', '6', '7', '8', '9', ':', ';', '<', '=', '>', '?', '@', 'A', 'B', 'C', 'D', 'E', 'F', 'G', 'H', 'I', 'J', 'K', 'L', 'M', 'N', 'O', 'P', 'Q', 'R', 'S', 'T', 'U', 'V', 'W', 'X', 'Y', 'Z', '[', '\\', ']', '^', '_', '`', 'a', 'b', 'c', 'd', 'e', 'f', 'g', 'h', 'i', 'j', 'k', 'l', 'm', 'n', 'o', 'p', 'q', 'r', 's', 't', 'u', 'v', 'w', 'x', 'y', 'z', '{', '|', '}', '~', '¡', '¢', '£', '¤', '¥', '¦', '§', '©', '«', '¬', '®', '°', '±', '¶', '·', '»', '¿', 'Â', 'Ã', 'Å', 'Ç', 'É', 'Ê', 'Ï', 'Ð', 'Ñ', 'Ö', '×', 'Ø', 'Ù', 'Ü', 'Þ', 'ß', 'à', 'á', 'â', 'ã', 'ä', 'å', 'æ', 'ç', 'è', 'é', 'ê', 'ë', 'í', 'î', 'ï', 'ñ', 'ò', 'ó', 'ô', 'õ', 'ö', '÷', 'ø', 'ù', 'ú', 'û', 'ü', 'ā', 'ă', 'Ą', 'ą', 'ć', 'ĉ', 'Č', 'č', 'ď', 'Đ', 'đ', 'ę', 'ğ', 'Ģ', 'ī', 'į', 'İ', 'ı', 'ĸ', 'Ļ', 'Ľ', 'Ł', 'ł', 'ŋ', 'ō', 'ő', 'Œ', 'œ', 'Ŗ', 'Ś', 'ś', 'ŝ', 'Ş', 'ş', 'Š', 'š', 'ţ

In [5]:
# Define your input array of embeddings
# input_embeddings = list(map(lambda x: int(x), dev.loc[0,"bertmsa"]))
input_embeddings = dev.loc[0,"bertmsa"]
# print(input_embeddings)
# Padding or truncating input embeddings to match BERT's input size (512)
max_length = 768
# Convert embeddings to torch tensor
# input_tensor = torch.tensor([input_embeddings[:max_length]])
input_tensor = torch.tensor(input_embeddings)
# input_ids = input_tensor.to(torch.int64)

print(input_tensor[0])

tensor(-1.0541)


In [6]:
tokens = tokenizer("أكمد", add_special_tokens = True, padding=True, truncation=True)



print(tokens)
with torch.no_grad():
    outputs = model(**tokens)

# Get the last hidden states
last_hidden_states = outputs.last_hidden_state

# Convert the last hidden states back to words
decoded_tokens = tokenizer.convert_ids_to_tokens(torch.argmax(last_hidden_states, dim=-1).squeeze().tolist())
decoded_text = tokenizer.convert_tokens_to_string(decoded_tokens)

print(decoded_text)

# print(model(""))

---------------------------------------------------------------------------
NameError                                 Traceback (most recent call last)
Cell In[1], line 1
----> 1 tokens = tokenizer("أكمد", add_special_tokens = True, padding=True, truncation=True)
      5 print(tokens)
      6 with torch.no_grad():

NameError: name 'tokenizer' is not defined


In [7]:
# print(tokenizer.decode(input_tensor))
# print(tokenizer.decode(input_ids))
# model(input_ids)
token_ids = tokenizer.convert_ids_to_tokens(torch.argmax(torch.tensor(input_tensor), dim=-1).squeeze().tolist())
print(token_ids)
decoded_text = tokenizer.convert_tokens_to_string(token_ids)
print(decoded_text)

# Decode embeddings back to words
# with torch.no_grad():
#     outputs = model(input_tensor)
#     print(outputs)
#     last_hidden_states = outputs[0]  # Get the last hidden states
#     # Convert the last hidden states back to tokens
#     decoded_tokens = tokenizer.convert_ids_to_tokens(torch.argmax(last_hidden_states, dim=-1).squeeze().tolist())
#     decoded_text = tokenizer.convert_tokens_to_string(decoded_tokens)

# print(decoded_text)

ø
ø


In [8]:
gloss_s = preprocess_text(dev["gloss"][0])
word_s = preprocess_text(dev["word"][0])
pos = dev["pos"][0]

encoding = tokenizer(word_s, gloss_s, add_special_tokens = True, max_length = 512 ,padding=True)#, padding=768)
print(encoding)

a = tokenizer.decode(encoding["input_ids"])
print(a)

{'input_ids': [2, 5983, 2368, 3, 11953, 20884, 1027, 3338, 3], 'token_type_ids': [0, 0, 0, 0, 1, 1, 1, 1, 1], 'attention_mask': [1, 1, 1, 1, 1, 1, 1, 1, 1]}
[CLS] أكمد [SEP] غم وأمرض القلب [SEP]


In [9]:
print(gloss_s)
print(tokenizer.tokenize(gloss_s))
print(tokenizer.convert_tokens_to_ids((tokenizer.tokenize(gloss_s))))

print(word_s)
print(tokenizer.tokenize(word_s))
print(tokenizer.convert_tokens_to_ids((tokenizer.tokenize(word_s))))


print(pos)
print(tokenizer.tokenize(pos))
print(tokenizer.convert_tokens_to_ids((tokenizer.tokenize(pos))))

غم وأمرض القلب
['غم', 'وأمر', '##ض', 'القلب']
[11953, 20884, 1027, 3338]
أكمد
['أك', '##مد']
[5983, 2368]
V
['V']
[58]


Convert all dev gloss to ids
°°°"""

dev_ids = [
        # tokenizer.convert_tokens_to_ids((
        #     tokenizer.tokenize(preprocess_text(gloss))))
        tokenizer(preprocess_text(word), preprocess_text(gloss), add_special_tokens = True, max_length = "512", padding=True, return_tensors="pt")
        for word, gloss in zip(dev["word"], dev["gloss"])
        ]

In [10]:
# Tokenize all of the sentences and map the tokens to thier word IDs.
dev_ids = []

# For every sentence...
for word, gloss in  zip(dev["word"], dev["gloss"]):
  # `encode` will:
    #   (1) Tokenize the sentence.
    #   (2) Prepend the `[CLS]` token to the start.
    #   (3) Append the `[SEP]` token to the end.
    #   (4) Map tokens to their IDs.
    dev_sent = tokenizer.encode(
                        preprocess_text(word), preprocess_text(gloss),                      # Sentence to encode.
                        add_special_tokens = True, # Add '[CLS]' and '[SEP]'
                        # This function also supports truncation and conversion
                        # to pytorch tensors, but we need to do padding, so we
                        # can't use these features :( .
                        max_length = 512,          # Truncate all sentences.
                        #return_tensors = 'pt',     # Return pytorch tensors.
                        padding=True,
                   )
    dev_ids.append(dev_sent)

print('Original: ', dev.loc[0,'word'],  dev.loc[0,'gloss'])
print('Token IDs:', dev_ids[0])
print(tokenizer.decode(dev_ids[0]))

Original:  أَكْمَدَ غَمَّ وَأَمْرَضَ القَلْبَ
Token IDs: [2, 5983, 2368, 3, 11953, 20884, 1027, 3338, 3]
[CLS] أكمد [SEP] غم وأمرض القلب [SEP]


In [11]:
print('Max sentence length: ', max([len(sen) for sen in dev_ids]))

Max sentence length:  95


In [12]:
print(dev_ids[0:5])

[[2, 5983, 2368, 3, 11953, 20884, 1027, 3338, 3], [2, 3, 5583, 7582, 19448, 1042, 1016, 3704, 5650, 19419, 19752, 3], [2, 5938, 1007, 3, 5938, 1007, 18435, 1043, 26049, 1007, 14832, 1913, 3], [2, 2690, 1009, 3, 2690, 1009, 5295, 1006, 3], [2, 4491, 1031, 3, 4491, 1031, 25381, 4449, 5722, 10066, 22148, 1031, 3]]


In [13]:
# dev_input_ids = list(map(lambda k: k["input_ids"], dev_ids))
# dev_mask_ids = list(map(lambda k: k["attention_mask"], dev_ids))
# dev_token_ids = list(map(lambda k: k["token_type_ids"], dev_ids))

dev_input_ids = []
dev_mask_ids = []
dev_token_ids = []

for _id in dev_ids:
    dev_input_ids.append(_id["input_ids"])
    dev_mask_ids.append(_id["attention_mask"])
    dev_token_ids.append(_id["token_type_ids"])

# print(dev_input_ids)

[[2, 5983, 2368, 3, 11953, 20884, 1027, 3338, 3], [2, 3, 5583, 7582, 19448, 1042, 1016, 3704, 5650, 19419, 19752, 3], [2, 5938, 1007, 3, 5938, 1007, 18435, 1043, 26049, 1007, 14832, 1913, 3], [2, 2690, 1009, 3, 2690, 1009, 5295, 1006, 3], [2, 4491, 1031, 3, 4491, 1031, 25381, 4449, 5722, 10066, 22148, 1031, 3], [2, 4319, 1027, 3, 4319, 1027, 28338, 19731, 6640, 24184, 19731, 3], [2, 1958, 1011, 3, 5234, 2437, 2595, 12352, 1958, 1011, 3156, 1916, 27003, 1958, 1011, 5453, 1033, 3], [2, 2432, 2095, 3, 22197, 18072, 3163, 3], [2, 6449, 10428, 3, 5304, 8262, 2426, 3306, 3], [2, 13131, 3, 5403, 2632, 4174, 3], [2, 3681, 3, 4653, 4069, 9332, 2717, 27335, 3593, 13473, 2717, 3], [2, 11502, 1028, 3, 13630, 2096, 6706, 4488, 2329, 3291, 1028, 3], [2, 13131, 3, 14615, 4319, 26150, 2990, 2328, 3], [2, 2894, 3, 2894, 2894, 4300, 25856, 15187, 1016, 2588, 12909, 3799, 12275, 2131, 1010, 23447, 1993, 3], [2, 9564, 3, 2621, 2519, 1028, 3], [2, 5270, 3, 10540, 18330, 5414, 2170, 2065, 6577, 2226, 3], [2

In [14]:
# Set the maximum sequence length.
# I've chosen 64 somewhat arbitrarily. It's slightly larger than the
# maximum training sentence length of 47...
MAX_LEN = 512

print('\nPadding/truncating all sentences to %d values...' % MAX_LEN)

print('\nPadding token: "{:}", ID: {:}'.format(tokenizer.pad_token, tokenizer.pad_token_id))

# Pad our input tokens with value 0.
# "post" indicates that we want to pad and truncate at the end of the sequence,
# as opposed to the beginning.
# train_ids = pad_sequences(train_ids, maxlen=MAX_LEN, dtype="long",
#                           value=0, truncating="post", padding="post")

dev_ids = pad_sequences(dev_ids, maxlen=MAX_LEN, dtype="long",
                          value=0, truncating="post", padding="post")

print(dev_input_ids)


# test_ids = pad_sequences(test_ids, maxlen=MAX_LEN, dtype="long",
#                           value=0, truncating="post", padding="post")

print('\nDone.')


Padding/truncating all sentences to 512 values...

Padding token: "[PAD]", ID: 0
[[    2  5983  2368 ...     0     0     0]
 [    2     3  5583 ...     0     0     0]
 [    2  5938  1007 ...     0     0     0]
 ...
 [    2 16511     3 ...     0     0     0]
 [    2  8216  1043 ...     0     0     0]
 [    2  2240  6496 ...     0     0     0]]

Done.


In [15]:
print('Max sentence length: ', max([len(sen) for sen in dev_ids]))
print(dev_ids)

Max sentence length:  512
[[    2  5983  2368 ...     0     0     0]
 [    2     3  5583 ...     0     0     0]
 [    2  5938  1007 ...     0     0     0]
 ...
 [    2 16511     3 ...     0     0     0]
 [    2  8216  1043 ...     0     0     0]
 [    2  2240  6496 ...     0     0     0]]


In [16]:
dev_masks = []
# For each sentence...
for sent in dev_ids:

    # Create the attention mask.
    #   - If a token ID is 0, then it's padding, set the mask to 0.
    #   - If a token ID is > 0, then it's a real token, set the mask to 1.
    att_mask = [int(token_id > 0) for token_id in sent]

    # Store the attention mask for this sentence.
    dev_masks.append(att_mask)

print(dev_masks)

[[1, 1, 1, 1, 1, 1, 1, 1, 1, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0,

In [ ]:
dev_inputs=torch.tensor(dev_ids)
# dev_labels = torch.tensor(dev['id'])
dev_masks = torch.tensor(dev_masks)
dev_index = torch.tensor(dev.index.tolist())

In [ ]:
from torch.utils.data import TensorDataset, DataLoader, RandomSampler, SequentialSampler


# The DataLoader needs to know our batch size for training, so we specify it
# here.
# For fine-tuning BERT on a specific task, the authors recommend a batch size of
# 16 or 32.

batch_size = 18

# Create the DataLoader for our training set.
train_data = TensorDataset(train_inputs, train_masks, train_labels)
train_sampler = RandomSampler(train_data)
train_dataloader = DataLoader(train_data, sampler=train_sampler, batch_size=batch_size)

# Create the DataLoader for our validation set.
validation_data = TensorDataset(dev_inputs, dev_masks, dev_labels, dev_index)
validation_sampler = SequentialSampler(validation_data)
validation_dataloader = DataLoader(validation_data, sampler=validation_sampler, batch_size=batch_size)



# Create the DataLoader.
# prediction_data = TensorDataset(test_inputs, test_masks, test_labels, test_index)
# prediction_sampler = SequentialSampler(prediction_data)
# prediction_dataloader = DataLoader(prediction_data, sampler=prediction_sampler, batch_size=batch_size)

this for RDTASK

In [6]:
# 1. Prepare your dataset
dataset = JSONDataset(file='dev.json')
print(dataset)

In [7]:
# 2. Initialize a DataLoader
dataloader = get_dataloader(dataset, batch_size=32, shuffle=True)


print(dataloader)

class Args:
    def __init__(self):
        self.resume_train = False  # Whether to resume training from a saved model
        self.model_name = "CAMeL-Lab/bert-base-arabic-camelbert-msa"  # Pre-trained model name or path
        # self.model_name = "bert-base-uncased"  # Pre-trained model name or path
        
        self.max_len = 512  # Maximum sequence length
        self.from_pretrained = 1


# Initialize args object
args = Args()

In [8]:
# 3. Define and instantiate your model
# model = AraT5RevDict(args)
model = ARBERTRevDict(args)
# model = RevdictModel()
# 4. Set up your training loop
optimizer = torch.optim.Adam(model.parameters(), lr=0.001)
# loss_function = nn.CrossEntropyLoss()
loss_function = nn.CrossEntropyLoss()


num_epochs = 10

# 5. Train your model
for epoch in range(num_epochs):
    for batch in dataloader:
#         input_ids = batch['input_ids']
#         attention_mask = batch['attention_mask']
#         labels = batch['labels']
#         print(input_ids, attention_mask, labels)
        print(batch.keys())
        # optimizer.zero_grad()
        # loss, _ = model(input_ids, attention_mask, labels)
        # loss.backward()
        # optimizer.step()
        break
    break

    print(f'Epoch {epoch+1}/{num_epochs}, Loss: {loss.item()}')

# 6. Evaluate your model (optional)
# You can perform evaluation on a separate validation set using a similar process as training, 
# but using the model to predict outputs and comparing them to ground truth labels.

defaultdict(<class 'list'>, {'id': ['ar.963612', 'ar.13488', 'ar.997004'], 'word': ['يَسْتَبْشِر', 'خَرْج', 'قربة'], 'pos': ['V', 'noun', 'N'], 'gloss': ['فعل مضارع مزيد من الفعل (اِسْتَبْشَرَ)', 'شدّة الصَّوت المكبّر الخارج من جهاز تقوية الصَّوت.', 'كيس من المطاط ونحوه يملأ بماء ساخن يستعمل للتدفئة.'], 'electra': [[-1.5044341087, -0.6818116307, -0.6058294773, 0.1083872467, 0.1009726748, -0.3505160511, -0.4623017907, -0.2557604313, -0.035786882, -0.0362772606, 0.5783321857, 0.1728272885, 0.19512631, -0.2932312787, -0.1771386862, -0.049704913, -0.026923025, 0.400189817, -0.152488023, 0.1700449735, -0.2812029123, 0.1995341331, -0.6122121215, 0.2344987988, -0.1577478945, -0.2043482363, 0.5278186202, -0.3274523914, 0.3095464408, 0.5288835764, 0.354013592, -0.6328273416, 0.2034107298, 0.3988435864, 0.0740463063, 0.3995346427, -0.075540103, 0.0686714128, -0.4530136883, 0.1071773991, -0.6717195511, 0.4359377623, -0.5571882129, 0.4328630865, 0.6087440252, 1.3988630772, -0.9270292521, 0.4963251

RuntimeError: stack expects a non-empty TensorList

a
